# London Neighbourhoods by Most Common Businesses and Average Income #

## 1. Introduction ##

### 1.1 Background ###

Before opening a business, it is a good practice to analyse the market and the profile of potential customers. London is a very touristic city and have a vast offer of businesses and venues.
It is important to consider the profile of the population and how popular each venue category is in the area.

### 1.2 Problem ###

A customer would like to open a new Bakery in one of London Zone 1 neighbourhoods. He would like to be located in an above average income area and near to Hotels and other touristic spots.

### 1.3 Interest ###

In this report, the neighbourhoods in the region of London Zone 1 are analysed regarding their most common venue categories and average income of its population.
This report will classify the city neighbourhoods into clusters considering the data available about current businesses in the area and the average income of each neighbourhood. Then, it will be possible to assess the profile of that area of the city and give some insights about the potential businesses and customers.

## 2. Data ##

The data of London neighbourhoods is available from a postcode database in the website https://www.doogal.co.uk/ that combines data from the Royal Mail, OS and National Statistics. Using the Foursquare developer API it is possible to explore venues around each neighbourhood. Due to the limitation of 500 requests per hour for the free tier of the developer API, the analysis had to be restricted to London Zone 1.


In [1]:
import pandas as pd
pd.set_option('display.max_columns', None)
pd.set_option('display.max_rows', None)
import requests

### 2.1 Retrieve Data from Source ###

In [2]:
!wget -O london.csv "https://www.doogal.co.uk/UKPostcodesCSV.ashx?area=London"

--2020-04-24 21:33:03--  https://www.doogal.co.uk/UKPostcodesCSV.ashx?area=London
Resolving www.doogal.co.uk (www.doogal.co.uk)... 109.228.61.150
Connecting to www.doogal.co.uk (www.doogal.co.uk)|109.228.61.150|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: unspecified [text/plain]
Saving to: ‘london.csv’

london.csv              [          <=>       ] 142.95M  11.8MB/s    in 13s     

2020-04-24 21:33:22 (10.9 MB/s) - ‘london.csv’ saved [149893032]



### 2.2 Build Dataframe and Examine Data ###

In [3]:
londonpc = pd.read_csv("london.csv", delimiter=",")
londonpc.shape

(321834, 47)

In [4]:
londonpc.head()

Postcode In Use?   Latitude  Longitude  Easting  Northing  Grid Ref  \
0  BR1 1AA     Yes  51.401546   0.015415   540291    168873  TQ402688   
1  BR1 1AB     Yes  51.406333   0.015208   540262    169405  TQ402694   
2  BR1 1AD      No  51.400057   0.016715   540386    168710  TQ403687   
3  BR1 1AE     Yes  51.404543   0.014195   540197    169204  TQ401692   
4  BR1 1AF     Yes  51.401392   0.014948   540259    168855  TQ402688   

           County District          Ward District Code  Ward Code  Country  \
0  Greater London  Bromley  Bromley Town     E09000006  E05000109  England   
1  Greater London  Bromley  Bromley Town     E09000006  E05000109  England   
2  Greater London  Bromley  Bromley Town     E09000006  E05000109  England   
3  Greater London  Bromley  Bromley Town     E09000006  E05000109  England   
4  Greater London  Bromley  Bromley Town     E09000006  E05000109  England   

  County Code             Constituency  Introduced  Terminated  \
0   E11000009  Bromley and Chislehurst  2016-05-01         NaN   
1   E11000009  Bromley and Chislehurst  2012-03-01         NaN   
2   E11000009  Bromley and Chislehurst  2014-09-01  2017-09-01   
3   E11000009  Bromley and Chislehurst  2008-08-01         NaN   
4   E11000009  Bromley and Chislehurst  2015-05-01         NaN   

                     Parish  National Park  Population  Households  \
0  Bromley, unparished area            NaN         NaN         NaN   
1  Bromley, unparished area            NaN         NaN         NaN   
2  Bromley, unparished area            NaN         NaN         NaN   
3  Bromley, unparished area            NaN        34.0        21.0   
4  Bromley, unparished area            NaN         NaN         NaN   

    Built up area Built up sub-division Lower layer super output area  \
0  Greater London               Bromley                  Bromley 018B   
1  Greater London               Bromley                  Bromley 008B   
2  Greater London               Bromley                  Bromley 018B   
3  Greater London               Bromley                  Bromley 018C   
4  Greater London               Bromley                  Bromley 018B   

               Rural/urban  Region  Altitude  London zone  LSOA Code  \
0  Urban major conurbation  London        71            5  E01000675   
1  Urban major conurbation  London        71            4  E01000676   
2  Urban major conurbation  London        53            5  E01000675   
3  Urban major conurbation  London        71            4  E01000677   
4  Urban major conurbation  London        58            5  E01000675   

   Local authority  MSOA Code Middle layer super output area Parish Code  \
0              NaN  E02000144                    Bromley 018   E43000196   
1              NaN  E02000134                    Bromley 008   E43000196   
2              NaN  E02000144                    Bromley 018   E43000196   
3              NaN  E02000144                    Bromley 018   E43000196   
4              NaN  E02000144                    Bromley 018   E43000196   

  Census output area Constituency Code  Index of Multiple Deprivation  \
0          E00003264         E14000604                          24305   
1          E00003255         E14000604                          13716   
2          E00003264         E14000604                          24305   
3          E00003266         E14000604                          20694   
4          E00003264         E14000604                          24305   

   Quality  User Type Last updated Nearest station  Distance to station  \
0        1          0   2020-02-19   Bromley South             0.218257   
1        1          0   2020-02-19   Bromley North             0.253666   
2        1          1   2020-02-19   Bromley South             0.044559   
3        1          0   2020-02-19   Bromley North             0.462939   
4        1          0   2020-02-19   Bromley South             0.227664   

  Postcode area Postcode district         Police force Wa

### 2.3 Data Cleaning ###

First, it is important to check the consistency of the data. The postcodes that are not active are removed and the data is restricted to London Zone 1.

In [5]:
londonpc= londonpc[londonpc['In Use?']=='Yes'].reset_index()
londonpc.shape

(178631, 48)

In [6]:
londonpc= londonpc[londonpc['London zone']<=1].reset_index()
londonpc.shape

(26929, 49)

Now, only columns that have important data for the analysis are kept.

In [7]:
neighborhoods=londonpc.filter(['Postcode area', 'Postcode district', 'Postcode', 'Latitude', 'Longitude', 'Ward', 'Average Income'])
neighborhoods.head(5)

Postcode area Postcode district Postcode   Latitude  Longitude         Ward  \
0             E                E1   E1 1AB  51.512262  -0.066722  Whitechapel   
1             E                E1   E1 1AE  51.516174  -0.066181  Whitechapel   
2             E                E1   E1 1AF  51.512262  -0.066722  Whitechapel   
3             E                E1   E1 1AG  51.516028  -0.066014  Whitechapel   
4             E                E1   E1 1AJ  51.514677  -0.067556  Whitechapel   

   Average Income  
0           65300  
1           65300  
2           65300  
3           65300  
4           65300

In [8]:
neighborhoods.shape

(26929, 7)

The Average Income is part of this analysis, hence it is important to check for missing data.

In [9]:
neighborhoods['Average Income'].describe()

count    26929.000000
mean     57121.764640
std       9000.986184
min      38500.000000
25%      52200.000000
50%      54300.000000
75%      61900.000000
max      74200.000000
Name: Average Income, dtype: float64

In [10]:
neighborhoods.shape

(26929, 7)

### 2.4 Feature Selection ###

The dataframe has data of each postcode in London Zone 1. In order to simplify the analysis, let's group this data by the Postcode District and Ward around the mean coordinates of the area.

In [11]:
inner_grouped = neighborhoods.groupby(['Postcode district', 'Ward']).mean().reset_index()
inner_grouped.head()

Postcode district                       Ward   Latitude  Longitude  \
0                E1                    Aldgate  51.515409  -0.078265   
1                E1                Bishopsgate  51.517967  -0.078461   
2                E1   Hoxton East & Shoreditch  51.524272  -0.077455   
3                E1                  Portsoken  51.514776  -0.075659   
4                E1  Spitalfields & Banglatown  51.518738  -0.073411   

   Average Income  
0    65400.000000  
1    65400.000000  
2    54300.000000  
3    65400.000000  
4    53360.930233

Finally, let's check the shape of the resulting dataframe.

In [12]:
inner_grouped.shape

(331, 5)

# 3. Methodology #

### 3.1 Exploratory Analysis ###

The dataframe built from the postcode data of London neighbourhoods contains the geographic coordinates for each Postcode District and Ward of London Zone 1 area. Using the Foursquare API, it is possible to explore nearby venues for each neighbourhood.

In [13]:
import numpy as np # library to handle data in a vectorized manner

import json # library to handle JSON files

!conda install -c conda-forge geopy --yes # uncomment this line if you haven't completed the Foursquare API lab
from geopy.geocoders import Nominatim # convert an address into latitude and longitude values

import requests # library to handle requests
from pandas.io.json import json_normalize # tranform JSON file into a pandas dataframe

# Matplotlib and associated plotting modules
import matplotlib.cm as cm
import matplotlib.colors as colors

# import k-means from clustering stage
from sklearn.cluster import KMeans

#!conda install -c conda-forge folium=0.5.0 --yes # uncomment this line if you haven't completed the Foursquare API lab
import folium # map rendering library

print('Libraries imported.')

Solving environment: done

# All requested packages already installed.

Libraries imported.


To illustrate the area of interest, the following map highlights each neighbourhood.

In [14]:
address = 'City of London, London'

geolocator = Nominatim(user_agent="britishexplorer")
location = geolocator.geocode(address)
latitude = location.latitude
longitude = location.longitude
print('The geograpical coordinate of London are {}, {}.'.format(latitude, longitude))

The geograpical coordinate of London are 51.5156177, -0.0919983.


In [15]:
# create map of Inner London using latitude and longitude values
map_london = folium.Map(location=[latitude, longitude], zoom_start=12)

# add markers to map
for lat, lng, postcode, district in zip(inner_grouped['Latitude'], inner_grouped['Longitude'], inner_grouped['Postcode district'], inner_grouped['Ward']):
    label = '{}, {}'.format(postcode, district)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

Now, it is possible to use the Foursquare API to explore the venues in each neighbourhood.

In [64]:
CLIENT_ID = 'hidden' # your Foursquare ID
CLIENT_SECRET = 'hidden' # your Foursquare Secret
VERSION = '20200101' # Foursquare API version

print('Your credentails:')
print('CLIENT_ID: ' + CLIENT_ID)
print('CLIENT_SECRET:' + CLIENT_SECRET)

Your credentails:
CLIENT_ID: hidden
CLIENT_SECRET:hidden


First, let's test with the first neighborhood.

In [23]:
inner_grouped.loc[0, 'Postcode district']

'E1'

In [24]:
neighborhood_latitude = inner_grouped.loc[0, 'Latitude'] # neighborhood latitude value
neighborhood_longitude = inner_grouped.loc[0, 'Longitude'] # neighborhood longitude value

neighborhood_name = inner_grouped.loc[0, 'Postcode district'] + ' ' + inner_grouped.loc[0, 'Ward'] # neighborhood name

print('Latitude and longitude values of {} are {}, {}.'.format(neighborhood_name, 
                                                               neighborhood_latitude, 
                                                               neighborhood_longitude))

Latitude and longitude values of E1 Aldgate are 51.515409, -0.07826466666666666.


In [25]:
radius=500
LIMIT=100
url = 'https://api.foursquare.com/v2/venues/explore?client_id={}&client_secret={}&ll={},{}&v={}&radius={}&limit={}&sortByPopularity=1'.format(CLIENT_ID, CLIENT_SECRET, neighborhood_latitude, neighborhood_longitude, VERSION, radius, LIMIT)

results = requests.get(url).json()
try:
    print('There are {} venues around {}.'.format(len(results['response']['groups'][0]['items']),neighborhood_name))
except:
    print('Error: ', results)

There are 100 venues around E1 Aldgate.


To simplify the collection of data for all neighbourhoods, it is best to define a function that extracts the category of the venues.

In [26]:
# function that extracts the category of the venue
def get_category_type(row):
    try:
        categories_list = row['categories']
    except:
        categories_list = row['venue.categories']
        
    if len(categories_list) == 0:
        return None
    else:
        return categories_list[0]['name']

In [27]:
venues = results['response']['groups'][0]['items']
    
nearby_venues = json_normalize(venues) # flatten JSON

# filter columns
filtered_columns = ['venue.name', 'venue.categories', 'venue.location.lat', 'venue.location.lng']
nearby_venues =nearby_venues.loc[:, filtered_columns]

# filter the category for each row
nearby_venues['venue.categories'] = nearby_venues.apply(get_category_type, axis=1)

# clean columns
nearby_venues.columns = [col.split(".")[-1] for col in nearby_venues.columns]

nearby_venues.head()

/home/jupyterlab/conda/envs/python/lib/python3.6/site-packages/ipykernel_launcher.py:3: FutureWarning: pandas.io.json.json_normalize is deprecated, use pandas.json_normalize instead
  This is separate from the ipykernel package so we can avoid doing imports until


name        categories  \
0                                         SUSHISAMBA  Sushi Restaurant   
1                                  Leadenhall Market            Market   
2  Andaz London Liverpool Street - a concept by H...             Hotel   
3                                      Duck & Waffle      Cocktail Bar   
4                                       The Culpeper               Pub   

         lat       lng  
0  51.516156 -0.081169  
1  51.512745 -0.083524  
2  51.517213 -0.081645  
3  51.516108 -0.080926  
4  51.516876 -0.073071

In [28]:
print('{} venues were returned by Foursquare.'.format(nearby_venues.shape[0]))

100 venues were returned by Foursquare.


Now, let's define a function that returns nearby venues for given coordinates.

In [29]:
def getNearbyVenues(names, latitudes, longitudes, LIMIT=100, radius=500):
    
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}&sortByPopularity=1'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results=[]
        trials=0
        while (results==[] and trials<15):
            try:
                results = requests.get(url).json()
                results=results["response"]['groups'][0]['items']
                trials=0
            except:
                print('Error: ', results)
                results=[]
                print(name)
                trials=trials+1
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

Using the combination of Postcode District and Ward, let's assign the Neighborhood column to identify each region.

In [30]:
inner_grouped['Neighborhood']=inner_grouped['Postcode district']+' '+inner_grouped['Ward']
inner_grouped.head()

Postcode district                       Ward   Latitude  Longitude  \
0                E1                    Aldgate  51.515409  -0.078265   
1                E1                Bishopsgate  51.517967  -0.078461   
2                E1   Hoxton East & Shoreditch  51.524272  -0.077455   
3                E1                  Portsoken  51.514776  -0.075659   
4                E1  Spitalfields & Banglatown  51.518738  -0.073411   

   Average Income                  Neighborhood  
0    65400.000000                    E1 Aldgate  
1    65400.000000                E1 Bishopsgate  
2    54300.000000   E1 Hoxton East & Shoreditch  
3    65400.000000                  E1 Portsoken  
4    53360.930233  E1 Spitalfields & Banglatown

From the Foursquare API, it is possible to get London venues for each Neighourhood.

In [31]:
london_venues = getNearbyVenues(names=inner_grouped['Neighborhood'],
                                   latitudes=inner_grouped['Latitude'],
                                   longitudes=inner_grouped['Longitude']
                                  )

E1 Aldgate
E1 Bishopsgate
E1 Hoxton East & Shoreditch
E1 Portsoken
E1 Spitalfields & Banglatown
E1 Tower
E1 Weavers
E1 Whitechapel
E1W St Katharine's & Wapping
E1W Whitechapel
E2 Haggerston
E2 Hoxton East & Shoreditch
E2 Weavers
E98 St Katharine's & Wapping
EC1A Aldersgate
EC1A Bread Street
EC1A Bunhill
EC1A Cheap
EC1A Clerkenwell
EC1A Farringdon Within
EC1A Farringdon Without
EC1M Bunhill
EC1M Clerkenwell
EC1M Cripplegate
EC1M Farringdon Within
EC1M Holborn and Covent Garden
EC1N Castle Baynard
EC1N Clerkenwell
EC1N Farringdon Without
EC1N Holborn and Covent Garden
EC1P Clerkenwell
EC1R Clerkenwell
EC1R Holborn and Covent Garden
EC1V Bunhill
EC1V Clerkenwell
EC1V Hoxton East & Shoreditch
EC1V Hoxton West
EC1V St Peter's
EC1Y Bunhill
EC1Y Clerkenwell
EC1Y Coleman Street
EC1Y Cripplegate
EC2A Bishopsgate
EC2A Bunhill
EC2A Clerkenwell
EC2A Hoxton East & Shoreditch
EC2M Bishopsgate
EC2M Broad Street
EC2M Bunhill
EC2M Clerkenwell
EC2M Coleman Street
EC2M Cornhill
EC2M Hoxton East & Shoredi

In [32]:
print(london_venues.shape)
london_venues.head()

(23098, 7)


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0   E1 Aldgate              51.515409               -0.078265   
1   E1 Aldgate              51.515409               -0.078265   
2   E1 Aldgate              51.515409               -0.078265   
3   E1 Aldgate              51.515409               -0.078265   
4   E1 Aldgate              51.515409               -0.078265   

                                               Venue  Venue Latitude  \
0                                         SUSHISAMBA       51.516156   
1                                  Leadenhall Market       51.512745   
2  Andaz London Liverpool Street - a concept by H...       51.517213   
3                                      Duck & Waffle       51.516108   
4                                       The Culpeper       51.516876   

   Venue Longitude    Venue Category  
0        -0.081169  Sushi Restaurant  
1        -0.083524            Market  
2        -0.081645             Hotel  
3        -0.080926      Cocktail Bar  
4        -0.073071               Pub

Some venue categories are not relevant for the analysis, such as public transportation venues. Thus, let's remove those from the dataframe.

In [33]:
print(london_venues.shape)
london_venues=london_venues[london_venues['Venue Category']!='Bus Stop']
london_venues=london_venues[london_venues['Venue Category']!='Bus Station']
london_venues=london_venues[london_venues['Venue Category']!='Metro Station']
print(london_venues.shape)

(23098, 7)
(23047, 7)


Now, let's count venues by neighborhood.

In [34]:
london_venues.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                  
E1 Aldgate                                              100   
E1 Bishopsgate                                           76   
E1 Hoxton East & Shoreditch                             100   
E1 Portsoken                                            100   
E1 Spitalfields & Banglatown                             55   
E1 Tower                                                 55   
E1 Weavers                                               65   
E1 Whitechapel                                           95   
E1W St Katharine's & Wapping                             67   
E1W Whitechapel                                          42   
E2 Haggerston                                            46   
E2 Hoxton East & Shoreditch                              64   
E2 Weavers                                               86   
E98 St Katharine's & Wapping                             57   
EC1A Aldersgate                                          74   
EC1A Bread Street                                       100   
EC1A Bunhill                                             93   
EC1A Cheap                                              100   
EC1A Clerkenwell                                         68   
EC1A Farringdon Within                                   57   
EC1A Farringdon Without                                 100   
EC1M Bunhill                                             58   
EC1M Clerkenwell                                         86   
EC1M Cripplegate                                         94   
EC1M Farringdon Within                                   76   
EC1M Holborn and Covent Garden                           59   
EC1N Castle Baynard                                     100   
EC1N Clerkenwell                                         68   
EC1N Farringdon Without                                  95   
EC1N Holborn and Covent Garden                           86   
EC1P Clerkenwell                                         68   
EC1R Clerkenwell                                        100   
EC1R Holborn and Covent Garden                           81   
EC1V Bunhill                                             93   
EC1V Clerkenwell                                         99   
EC1V Hoxton East & Shoreditch                           100   
EC1V Hoxton West                                         86   
EC1V St Peter's                                          46   
EC1Y Bunhill                                             85   
EC1Y Clerkenwell                                         68   
EC1Y Coleman Street                                      44   
EC1Y Cripplegate                                         91   
EC2A Bishopsgate                                         35   
EC2A Bunhill                                             86   
EC2A Clerkenwell                                         68   
EC2A Hoxton East & Shoreditch                           100   
EC2M Bishopsgate                                         82   
EC2M Broad Street                                        74   
EC2M Bunhill                                             38   
EC2M Clerkenwell                                         68   
EC2M Coleman Street                                      49   
EC2M Cornhill                                           100   
EC2M Hoxton East & Shoreditch                            21   
EC2M Spitalfields & Banglatown                           56   
EC2N Bishopsgate                                        100   
EC2N Broad Street                                       100   
EC2N Clerkenwell                                         68   
EC2N Cornhill                                           100   
EC2N Lime Street                                        100   
EC2N Walbrook                                           100   
EC2P Bassishaw                                          100   
EC2P Bishopsgate                                         70   
EC2P C

It is possible to find out how many unique categories are found for this region in London.

In [35]:
print('There are {} uniques categories.'.format(len(london_venues['Venue Category'].unique())))

There are 330 uniques categories.


For each neighbourhood, a new dataframe shows how many venues of each category were found using Foursquare.

In [36]:
# one hot encoding
london_onehot = pd.get_dummies(london_venues[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
london_onehot['Neighborhood'] = london_venues['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [london_onehot.columns[-1]] + list(london_onehot.columns[:-1])
london_onehot = london_onehot[fixed_columns]

london_onehot.head()

Yoga Studio  Accessories Store  Adult Boutique  Afghan Restaurant  \
0            0                  0               0                  0   
1            0                  0               0                  0   
2            0                  0               0                  0   
3            0                  0               0                  0   
4            0                  0               0                  0   

   African Restaurant  American Restaurant  Animal Shelter  Antique Shop  \
0                   0                    0               0             0   
1                   0                    0               0             0   
2                   0                    0               0             0   
3                   0                    0               0             0   
4                   0                    0               0             0   

   Aquarium  Arcade  Arepa Restaurant  Argentinian Restaurant  Art Gallery  \
0         0       0                 0                       0            0   
1         0       0                 0                       0            0   
2         0       0                 0                       0            0   
3         0       0                 0                       0            0   
4         0       0                 0                       0            0   

   Art Museum  Arts & Crafts Store  Asian Restaurant  Athletics & Sports  \
0           0                    0                 0                   0   
1           0                    0                 0                   0   
2           0                    0                 0                   0   
3           0                    0                 0                   0   
4           0                    0                 0                   0   

   Australian Restaurant  Austrian Restaurant  BBQ Joint  Bagel Shop  Bakery  \
0                      0                    0          0           0       0   
1                      0                    0          0           0       0   
2                      0                    0          0           0       0   
3                      0                    0          0           0       0   
4                      0                    0          0           0       0   

   Bar  Basketball Court  Bathing Area  Beach  Bed & Breakfast  Beer Bar  \
0    0                 0             0      0                0         0   
1    0                 0             0      0                0         0   
2    0                 0             0      0                0         0   
3    0                 0             0      0                0         0   
4    0                 0             0      0                0         0   

   Beer Garden  Beer Store  Belgian Restaurant  Bike Rental / Bike Share  \
0            0           0                   0                         0   
1            0           0                   0                         0   
2            0           0                   0                         0   
3            0           0                   0                         0   
4            0           0                   0                         0   

   Bike Shop  Bistro  Boat or Ferry  Bookstore  Botanical Garden  Boutique  \
0          0       0              0          0                 0         0   
1          0       0              0          0                 0         0   
2          0       0              0          0                 0         0   
3          0       0              0          0                 0         0   
4          0       0              0          0                 0         0   

   Bowling Alley  Boxing Gym  Brasserie  Brazilian Restaurant  Breakfast Spot  \
0              0           0          0                     0               0   
1              0           0          0                     0               0   
2              0           0          0                     0               0   

In [37]:
london_onehot.shape

(23047, 330)

Now, let's group rows by neighborhood and by taking the mean of the frequency of occurrence of each category.

In [38]:
london_grouped = london_onehot.groupby('Neighborhood').mean().reset_index()
london_grouped

Neighborhood  Yoga Studio  Accessories Store  \
0                              E1 Aldgate     0.000000           0.000000   
1                          E1 Bishopsgate     0.000000           0.000000   
2             E1 Hoxton East & Shoreditch     0.000000           0.000000   
3                            E1 Portsoken     0.000000           0.000000   
4            E1 Spitalfields & Banglatown     0.000000           0.000000   
5                                E1 Tower     0.000000           0.000000   
6                              E1 Weavers     0.000000           0.015385   
7                          E1 Whitechapel     0.010526           0.000000   
8            E1W St Katharine's & Wapping     0.000000           0.000000   
9                         E1W Whitechapel     0.000000           0.000000   
10                          E2 Haggerston     0.021739           0.000000   
11            E2 Hoxton East & Shoreditch     0.015625           0.000000   
12                             E2 Weavers     0.023256           0.000000   
13           E98 St Katharine's & Wapping     0.000000           0.000000   
14                        EC1A Aldersgate     0.000000           0.000000   
15                      EC1A Bread Street     0.000000           0.000000   
16                           EC1A Bunhill     0.000000           0.000000   
17                             EC1A Cheap     0.000000           0.000000   
18                       EC1A Clerkenwell     0.000000           0.000000   
19                 EC1A Farringdon Within     0.000000           0.000000   
20                EC1A Farringdon Without     0.000000           0.000000   
21                           EC1M Bunhill     0.000000           0.000000   
22                       EC1M Clerkenwell     0.000000           0.000000   
23                       EC1M Cripplegate     0.000000           0.000000   
24                 EC1M Farringdon Within     0.000000           0.000000   
25         EC1M Holborn and Covent Garden     0.000000           0.000000   
26                    EC1N Castle Baynard     0.000000           0.000000   
27                       EC1N Clerkenwell     0.000000           0.000000   
28                EC1N Farringdon Without     0.000000           0.000000   
29         EC1N Holborn and Covent Garden     0.000000           0.000000   
30                       EC1P Clerkenwell     0.000000           0.000000   
31                       EC1R Clerkenwell     0.000000           0.000000   
32         EC1R Holborn and Covent Garden     0.000000           0.000000   
33                           EC1V Bunhill     0.010753           0.000000   
34                       EC1V Clerkenwell     0.000000           0.000000   
35          EC1V Hoxton East & Shoreditch     0.010000           0.000000   
36                       EC1V Hoxton West     0.034884           0.000000   
37                        EC1V St Peter's     0.021739           0.000000   
38                           EC1Y Bunhill     0.023529           0.000000   
39                       EC1Y Clerkenwell     0.000000           0.000000   
40                    EC1Y Coleman Street     0.000000           0.000000   
41                       EC1Y Cripplegate     0.000000           0.000000   
42                       EC2A Bishopsgate     0.000000           0.000000   
43                           EC2A Bunhill     0.011628           0.000000   
44                       EC2A Clerkenwell     0.000000           0.000000   
45          EC2A Hoxton East & Shoreditch     0.010000           0.000000   
46                       EC2M Bishopsgate     0.000000           0.000000   
47                      EC2M Broad Street     0.000000           0.000000   
48                           EC2M Bunhill     0.000000           0.000000   
49                       EC2M Clerkenwell     0.000000           0.000000   
50                    EC2M Coleman Street     0.000000           0.000000   
51                       

In [39]:
london_grouped.shape

(331, 330)

Next, let's print each neighborhood along with the top 5 most common venues.

In [40]:
num_top_venues = 5

for hood in london_grouped['Neighborhood']:
    print("----"+hood+"----")
    temp = london_grouped[london_grouped['Neighborhood'] == hood].T.reset_index()
    temp.columns = ['venue','freq']
    temp = temp.iloc[1:]
    temp['freq'] = temp['freq'].astype(float)
    temp = temp.round({'freq': 2})
    print(temp.sort_values('freq', ascending=False).reset_index(drop=True).head(num_top_venues))
    print('\n')

----E1 Aldgate----
                  venue  freq
0           Coffee Shop  0.10
1                 Hotel  0.06
2          Cocktail Bar  0.05
3  Gym / Fitness Center  0.05
4                   Pub  0.04


----E1 Bishopsgate----
            venue  freq
0     Coffee Shop  0.09
1  Sandwich Place  0.07
2      Restaurant  0.05
3            Café  0.04
4    Cocktail Bar  0.04


----E1 Hoxton East & Shoreditch----
                venue  freq
0        Cocktail Bar  0.07
1         Coffee Shop  0.07
2  Italian Restaurant  0.06
3                Café  0.05
4          Restaurant  0.04


----E1 Portsoken----
                  venue  freq
0                 Hotel  0.11
1           Coffee Shop  0.10
2                   Pub  0.10
3          Cocktail Bar  0.05
4  Gym / Fitness Center  0.04


----E1 Spitalfields & Banglatown----
               venue  freq
0        Coffee Shop  0.15
1              Hotel  0.05
2               Café  0.05
3  Indian Restaurant  0.05
4        Flea Market  0.04


----E1 Tower----
   

In order to simplify the analysis, let's define a function to sort venues in descending order.

In [41]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

Finally, let's create a dataframe with top 10 categories for each neighborhood.

In [42]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
neighborhoods_venues_sorted['Neighborhood'] = london_grouped['Neighborhood']

for ind in np.arange(london_grouped.shape[0]):
    neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(london_grouped.iloc[ind, :], num_top_venues)

neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0                    E1 Aldgate           Coffee Shop                 Hotel   
1                E1 Bishopsgate           Coffee Shop        Sandwich Place   
2   E1 Hoxton East & Shoreditch           Coffee Shop          Cocktail Bar   
3                  E1 Portsoken                 Hotel                   Pub   
4  E1 Spitalfields & Banglatown           Coffee Shop                  Café   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0  Gym / Fitness Center          Cocktail Bar      Sushi Restaurant   
1            Restaurant          Cocktail Bar  Gym / Fitness Center   
2    Italian Restaurant                  Café            Restaurant   
3           Coffee Shop          Cocktail Bar  Gym / Fitness Center   
4                 Hotel     Indian Restaurant                   Pub   

    6th Most Common Venue      7th Most Common Venue 8th Most Common Venue  \
0                     Pub             Sandwich Place     Indian Restaurant   
1                    Café   Mediterranean Restaurant     Indian Restaurant   
2  Furniture / Home Store                      Hotel           Art Gallery   
3        Sushi Restaurant  Middle Eastern Restaurant     Indian Restaurant   
4            Cocktail Bar                Pizza Place           Flea Market   

  9th Most Common Venue    10th Most Common Venue  
0           Salad Place                Restaurant  
1           Flea Market                  Beer Bar  
2        Sandwich Place                       Bar  
3        Sandwich Place       Japanese Restaurant  
4           Art Gallery  Mediterranean Restaurant

### 3.2 Classification of Neighbourhoods ###

The region of Inner London is composed by 8 postcode districts. Using the k-means clustering technique, it is possible to classify each neighbourhood based on the data collected.

Before applying the k-means technique, let's combine Average income information to the venues categories data.

In [43]:
london_grouped_income=pd.merge(left=london_grouped, right=inner_grouped, left_on='Neighborhood', right_on='Neighborhood')
london_grouped_income.drop(columns=['Postcode district', 'Ward', 'Latitude', 'Longitude'], inplace=True)
london_grouped_income.head()

Neighborhood  Yoga Studio  Accessories Store  \
0                    E1 Aldgate          0.0                0.0   
1                E1 Bishopsgate          0.0                0.0   
2   E1 Hoxton East & Shoreditch          0.0                0.0   
3                  E1 Portsoken          0.0                0.0   
4  E1 Spitalfields & Banglatown          0.0                0.0   

   Adult Boutique  Afghan Restaurant  African Restaurant  American Restaurant  \
0             0.0                0.0            0.000000                 0.01   
1             0.0                0.0            0.000000                 0.00   
2             0.0                0.0            0.000000                 0.00   
3             0.0                0.0            0.000000                 0.00   
4             0.0                0.0            0.018182                 0.00   

   Animal Shelter  Antique Shop  Aquarium  Arcade  Arepa Restaurant  \
0             0.0           0.0       0.0     0.0               0.0   
1             0.0           0.0       0.0     0.0               0.0   
2             0.0           0.0       0.0     0.0               0.0   
3             0.0           0.0       0.0     0.0               0.0   
4             0.0           0.0       0.0     0.0               0.0   

   Argentinian Restaurant  Art Gallery  Art Museum  Arts & Crafts Store  \
0                0.010000     0.000000         0.0                  0.0   
1                0.013158     0.000000         0.0                  0.0   
2                0.000000     0.030000         0.0                  0.0   
3                0.010000     0.010000         0.0                  0.0   
4                0.000000     0.036364         0.0                  0.0   

   Asian Restaurant  Athletics & Sports  Australian Restaurant  \
0              0.02                 0.0                    0.0   
1              0.00                 0.0                    0.0   
2              0.01                 0.0                    0.0   
3              0.01                 0.0                    0.0   
4              0.00                 0.0                    0.0   

   Austrian Restaurant  BBQ Joint  Bagel Shop  Bakery   Bar  Basketball Court  \
0                  0.0   0.010000        0.00    0.01  0.00               0.0   
1                  0.0   0.013158        0.00    0.00  0.00               0.0   
2                  0.0   0.020000        0.01    0.00  0.03               0.0   
3                  0.0   0.010000        0.00    0.01  0.00               0.0   
4                  0.0   0.018182        0.00    0.00  0.00               0.0   

   Bathing Area  Beach  Bed & Breakfast  Beer Bar  Beer Garden  Beer Store  \
0           0.0    0.0              0.0  0.020000          0.0         0.0   
1           0.0    0.0              0.0  0.026316          0.0         0.0   
2           0.0    0.0              0.0  0.010000          0.0         0.0   
3           0.0    0.0              0.0  0.000000          0.0         0.0   
4           0.0    0.0              0.0  0.018182          0.0         0.0   

   Belgian Restaurant  Bike Rental / Bike Share  Bike Shop  Bistro  \
0                 0.0                       0.0       0.00     0.0   
1                 0.0                       0.0       0.00     0.0   
2                 0.0                       0.0       0.01     0.0   
3                 0.0                       0.0       0.00     0.0   
4                 0.0                       0.0       0.00     0.0   

   Boat or Ferry  Bookstore  Botanical Garden  Boutique  Bowling Alley  \
0            0.0   0.010000               0.0      0.00            0.0   
1            0.0   0.000000               0.0      0.00            0.0   
2            0.0   0.010000               0.0      0.01            0.0   
3            0.0   0.000000               0.0      0.00            0.0   
4            0.0   0.018182               0.0      0.00            0.0   

   Boxing Gym  Brasserie  Brazil

Using the sklearn package, let's apply k-means clustering technique to classify London Zone 1 neighbourhoods.

In [44]:
# set number of clusters
kclusters = 8

london_grouped_clustering = london_grouped_income.drop('Neighborhood', 1)

# run k-means clustering
kmeans = KMeans(n_clusters=kclusters, random_state=0).fit(london_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans.labels_[0:10] 

array([0, 0, 4, 0, 4, 0, 2, 0, 0, 6], dtype=int32)

In [45]:
# add clustering labels
neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans.labels_)
london_merged=[]
# merge toronto_grouped with toronto_data to add latitude/longitude for each neighborhood
london_merged = pd.merge(left=inner_grouped, right=neighborhoods_venues_sorted, left_on='Neighborhood', right_on='Neighborhood') #london_merged.join(neighborhoods_venues_sorted.set_index('Neighborhood'), on='Neighborhood')

In [46]:
london_merged.head() # check the last columns!

Postcode district                       Ward   Latitude  Longitude  \
0                E1                    Aldgate  51.515409  -0.078265   
1                E1                Bishopsgate  51.517967  -0.078461   
2                E1   Hoxton East & Shoreditch  51.524272  -0.077455   
3                E1                  Portsoken  51.514776  -0.075659   
4                E1  Spitalfields & Banglatown  51.518738  -0.073411   

   Average Income                  Neighborhood  Cluster Labels  \
0    65400.000000                    E1 Aldgate               0   
1    65400.000000                E1 Bishopsgate               0   
2    54300.000000   E1 Hoxton East & Shoreditch               4   
3    65400.000000                  E1 Portsoken               0   
4    53360.930233  E1 Spitalfields & Banglatown               4   

  1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0           Coffee Shop                 Hotel  Gym / Fitness Center   
1           Coffee Shop        Sandwich Place            Restaurant   
2           Coffee Shop          Cocktail Bar    Italian Restaurant   
3                 Hotel                   Pub           Coffee Shop   
4           Coffee Shop                  Café                 Hotel   

  4th Most Common Venue 5th Most Common Venue   6th Most Common Venue  \
0          Cocktail Bar      Sushi Restaurant                     Pub   
1          Cocktail Bar  Gym / Fitness Center                    Café   
2                  Café            Restaurant  Furniture / Home Store   
3          Cocktail Bar  Gym / Fitness Center        Sushi Restaurant   
4     Indian Restaurant                   Pub            Cocktail Bar   

       7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
0             Sandwich Place     Indian Restaurant           Salad Place   
1   Mediterranean Restaurant     Indian Restaurant           Flea Market   
2                      Hotel           Art Gallery        Sandwich Place   
3  Middle Eastern Restaurant     Indian Restaurant        Sandwich Place   
4                Pizza Place           Flea Market           Art Gallery   

     10th Most Common Venue  
0                Restaurant  
1                  Beer Bar  
2                       Bar  
3       Japanese Restaurant  
4  Mediterranean Restaurant

# 4. Results #

The following map shows the resulting clusters for each neighbourhood in London Zone 1.

In [47]:
# create map
map_clusters = folium.Map(location=[latitude, longitude], zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(london_merged['Latitude'], london_merged['Longitude'], london_merged['Neighborhood'], london_merged['Cluster Labels']):
    label = folium.Popup(str(poi) + ' Cluster ' + str(cluster), parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[cluster-1],
        fill=True,
        fill_color=rainbow[cluster-1],
        fill_opacity=0.7).add_to(map_clusters)
       
map_clusters

### 4.1 Examine Clusters

First, let's print the clusters of neighbourhoods associated with their average income and similar venues.

In [48]:
london_merged.loc[london_merged['Cluster Labels'] == 0, london_merged.columns[[5, 4] + list(range(6, london_merged.shape[1]))]]

Neighborhood  Average Income  Cluster Labels  \
0                             E1 Aldgate    65400.000000               0   
1                         E1 Bishopsgate    65400.000000               0   
3                           E1 Portsoken    65400.000000               0   
5                               E1 Tower    65400.000000               0   
7                         E1 Whitechapel    64446.606335               0   
8           E1W St Katharine's & Wapping    68534.782609               0   
14                       EC1A Aldersgate    65400.000000               0   
15                     EC1A Bread Street    65400.000000               0   
17                            EC1A Cheap    65400.000000               0   
19                EC1A Farringdon Within    65400.000000               0   
20               EC1A Farringdon Without    65400.000000               0   
23                      EC1M Cripplegate    65400.000000               0   
24                EC1M Farringdon Within    65400.000000               0   
26                   EC1N Castle Baynard    65400.000000               0   
28               EC1N Farringdon Without    65400.000000               0   
37                       EC1V St Peter's    63500.000000               0   
40                   EC1Y Coleman Street    65400.000000               0   
41                      EC1Y Cripplegate    65400.000000               0   
42                      EC2A Bishopsgate    65400.000000               0   
46                      EC2M Bishopsgate    65400.000000               0   
47                     EC2M Broad Street    65400.000000               0   
50                   EC2M Coleman Street    65400.000000               0   
51                         EC2M Cornhill    65400.000000               0   
54                      EC2N Bishopsgate    65400.000000               0   
55                     EC2N Broad Street    65400.000000               0   
57                         EC2N Cornhill    65400.000000               0   
58                      EC2N Lime Street    65400.000000               0   
59                         EC2N Walbrook    65400.000000               0   
60                        EC2P Bassishaw    65400.000000               0   
61                      EC2P Bishopsgate    65400.000000               0   
63                        EC2R Bassishaw    65400.000000               0   
64                     EC2R Broad Street    65400.000000               0   
65                            EC2R Cheap    65400.000000               0   
67                   EC2R Coleman Street    65400.000000               0   
68                       EC2R Cordwainer    65400.000000               0   
69                         EC2R Cornhill    65400.000000               0   
70                         EC2R Walbrook    65400.000000               0   
71                       EC2V Aldersgate    65400.000000               0   
72                        EC2V Bassishaw    65400.000000               0   
73                     EC2V Bread Street    65400.000000               0   
74                            EC2V Cheap    65400.000000               0   
76                   EC2V Coleman Street    65400.000000               0   
77                       EC2V Cordwainer    65400.000000               0   
78                         EC2V Walbrook    65400.000000               0   
79                       EC2Y Aldersgate    65400.000000               0   
80                        EC2Y Bassishaw    65400.000000               0   
83                   EC2Y Coleman Street    65400.000000               0   
84                      EC2Y Cripplegate    65400.000000               0   
85                          EC3A Aldgate    65400.000000               0   
86                      EC3A Bishopsgate    65400.000000               0   
88                      EC3A Lime Street    65400.000000               0   
89                        EC3A Portsoken    65400.000000               0   


In [49]:
london_merged.loc[london_merged['Cluster Labels'] == 0].describe()

Latitude   Longitude  Average Income  Cluster Labels
count  113.000000  113.000000      113.000000           113.0
mean    51.513680   -0.097749    65465.984868             0.0
std      0.006849    0.026954      781.249090             0.0
min     51.488437   -0.201006    62733.333333             0.0
25%     51.512031   -0.098656    65400.000000             0.0
50%     51.514163   -0.090758    65400.000000             0.0
75%     51.516527   -0.082921    65400.000000             0.0
max     51.536624   -0.068635    68758.883249             0.0

In [50]:
london_merged.loc[london_merged['Cluster Labels'] == 1, london_merged.columns[[5, 4] + list(range(6, london_merged.shape[1]))]]

Neighborhood  Average Income  Cluster Labels  \
10                    E2 Haggerston    51410.638298               1   
12                       E2 Weavers    51908.823529               1   
25   EC1M Holborn and Covent Garden    50000.000000               1   
29   EC1N Holborn and Covent Garden    50009.459459               1   
32   EC1R Holborn and Covent Garden    50000.000000               1   
33                     EC1V Bunhill    51123.410405               1   
38                     EC1Y Bunhill    49269.811321               1   
43                     EC2A Bunhill    48900.000000               1   
48                     EC2M Bunhill    48900.000000               1   
81                     EC2Y Bunhill    48900.000000               1   
151                   N1 Caledonian    48751.694915               1   
152                  N1 Clerkenwell    50900.000000               1   
174              SE1 North Walworth    49682.352941               1   
177                 SE1 St George's    48715.000000               1   
178                   SE11 Bishop's    50197.872340               1   
194                    SW1E Warwick    50300.000000               1   
200                  SW1V Churchill    50979.207921               1   
205                  SW1W Churchill    50300.000000               1   
210                    SW1W Warwick    50300.000000               1   
231                    SW8 Larkhall    49100.000000               1   
236                  SW95 Stockwell    49900.000000               1   
292                 WC1A Bloomsbury    50200.000000               1   
294  WC1A Holborn and Covent Garden    50200.000000               1   
295                 WC1B Bloomsbury    49691.588785               1   
297  WC1B Holborn and Covent Garden    50200.000000               1   
305  WC1N Holborn and Covent Garden    50028.571429               1   
307  WC1R Holborn and Covent Garden    50197.727273               1   
310  WC1V Holborn and Covent Garden    50200.000000               1   
311                WC1X Clerkenwell    51885.436893               1   
312  WC1X Holborn and Covent Garden    50053.164557               1   
316  WC2A Holborn and Covent Garden    50200.000000               1   
319  WC2B Holborn and Covent Garden    50200.000000               1   
324  WC2H Holborn and Covent Garden    50200.000000               1   

     1st Most Common Venue          2nd Most Common Venue  \
10                    Café                    Coffee Shop   
12                    Café                    Coffee Shop   
25             Coffee Shop                            Pub   
29                     Pub                    Coffee Shop   
32                     Pub                    Coffee Shop   
33             Coffee Shop                            Pub   
38             Coffee Shop           Gym / Fitness Center   
43             Coffee Shop           Gym / Fitness Center   
48    Gym / Fitness Center                     Food Truck   
81              Food Truck                    Coffee Shop   
151                   Café                   Burger Joint   
152                    Pub  Vegetarian / Vegan Restaurant   
174                   Park                            Pub   
177                    Pub                          Hotel   
178                    Pub                          Hotel   
194         Sandwich Place                    Coffee Shop   
200                  Hotel                           Café   
205     Italian Restaurant                         Bakery   
210                  Hotel                    Coffee Shop   
231  Portuguese Restaurant                            Pub   
236  Portuguese Restaurant                            Pub   
292            Coffee Shop                        Theater   
294            Coffee Shop                        Theater   
295            Coffee Shop                           Café   
297                   Café                 Sandwich Place   
305            Coffee 

In [51]:
london_merged.loc[london_merged['Cluster Labels'] == 1].describe()

Latitude  Longitude  Average Income  Cluster Labels
count  33.000000  33.000000       33.000000            33.0
mean   51.513192  -0.113951    50084.992729             1.0
std     0.016039   0.019780      810.122673             0.0
min    51.474929  -0.151341    48715.000000             1.0
25%    51.498447  -0.126297    49691.588785             1.0
50%    51.519364  -0.114378    50197.872340             1.0
75%    51.522302  -0.104450    50300.000000             1.0
max    51.533760  -0.071833    51908.823529             1.0

In [52]:
london_merged.loc[london_merged['Cluster Labels'] == 2, london_merged.columns[[5, 4] + list(range(6, london_merged.shape[1]))]]

Neighborhood  Average Income  Cluster Labels  \
6                          E1 Weavers    58200.000000               2   
168                 NW8 Regent's Park    55542.307692               2   
170            SE1 Borough & Bankside    55680.100756               2   
179                         SE11 Oval    56727.272727               2   
192                   SW1E St James's    57889.610390               2   
193               SW1E Vincent Square    57500.000000               2   
196                   SW1H St James's    57516.853933               2   
198                   SW1P St James's    57500.000000               2   
206  SW1W Knightsbridge and Belgravia    56300.000000               2   
209                   SW1W St James's    57500.000000               2   
212  SW1X Knightsbridge and Belgravia    56300.000000               2   
220   SW3 Knightsbridge and Belgravia    56300.000000               2   
222                       SW3 Stanley    56199.444444               2   
229   SW7 Knightsbridge and Belgravia    56300.000000               2   
232                          SW8 Oval    55577.777778               2   
237                     W11 Bayswater    56500.000000               2   
239                      W11 Colville    57685.714286               2   
249                      W1C West End    58105.263158               2   
262                      W1J West End    58075.987842               2   
263   W1K Knightsbridge and Belgravia    56300.000000               2   
266                      W1S West End    55594.076655               2   
276        W1W Marylebone High Street    57071.917808               2   
278                      W2 Bayswater    56500.000000               2   
282                      W2 Hyde Park    57946.315789               2   
283    W2 Knightsbridge and Belgravia    56300.000000               2   

    1st Most Common Venue  2nd Most Common Venue 3rd Most Common Venue  \
6             Coffee Shop                   Café  Gym / Fitness Center   
168        Cricket Ground                   Café            Hookah Bar   
170                 Hotel            Coffee Shop                   Pub   
179        Cricket Ground                   Café                   Pub   
192           Coffee Shop                  Hotel               Theater   
193                 Hotel            Coffee Shop                   Pub   
196                 Hotel      Outdoor Sculpture           Coffee Shop   
198           Coffee Shop                   Café                 Hotel   
206                  Café     Italian Restaurant                   Pub   
209           Coffee Shop                Theater  Gym / Fitness Center   
212                 Hotel               Boutique                  Café   
220                  Café               Boutique                 Hotel   
222    English Restaurant    American Restaurant                Bakery   
229                  Café     Italian Restaurant                Garden   
232           Coffee Shop  Portuguese Restaurant                  Café   
237                   Pub                  Hotel            Restaurant   
239                   Pub     Italian Restaurant                  Café   
249                 Hotel      French Restaurant          Burger Joint   
262                 Hotel               Boutique           Art Gallery   
263                 Hotel                   Café    Italian Restaurant   
266        Clothing Store           Cocktail Bar           Art Gallery   
276           Coffee Shop                    Pub            Restaurant   
278                   Pub                   Café           Coffee Shop   
282                 Hotel            Coffee Shop    Italian Restaurant   
283              Fountain      Outdoor Sculpture           Art Gallery   

         4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
6                        Hotel     Indian Restaurant        Clothing Store   
168                        Pub               

In [53]:
london_merged.loc[london_merged['Cluster Labels'] == 2].describe()

Latitude  Longitude  Average Income  Cluster Labels
count  25.000000  25.000000       25.000000            25.0
mean   51.504937  -0.150032    56844.505730             2.0
std     0.011694   0.029125      875.974124             0.0
min    51.482042  -0.201188    55542.307692             2.0
25%    51.497915  -0.170318    56300.000000             2.0
50%    51.504128  -0.147630    56500.000000             2.0
75%    51.513911  -0.138700    57516.853933             2.0
max    51.527610  -0.073314    58200.000000             2.0

In [54]:
london_merged.loc[london_merged['Cluster Labels'] == 3, london_merged.columns[[5, 4] + list(range(6, london_merged.shape[1]))]]

Neighborhood  Average Income  Cluster Labels  \
155                 N1 King's Cross    42300.000000               3   
158  N1C St Pancras and Somers Town    40700.000000               3   
161               NW1 Church Street    39800.000000               3   
162                NW1 King's Cross    40227.272727               3   
165  NW1 St Pancras and Somers Town    40700.000000               3   
166              NW1W Regent's Park    41300.000000               3   
167               NW8 Church Street    39800.000000               3   
281                W2 Church Street    39800.000000               3   
285                W2 Little Venice    39800.000000               3   
302               WC1H King's Cross    39218.918919               3   
303                 WC1N Bloomsbury    43450.847458               3   
306               WC1N King's Cross    39725.806452               3   
313               WC1X King's Cross    42300.000000               3   

    1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
155           Coffee Shop                  Café                 Hotel   
158                  Café                   Pub           Coffee Shop   
161           Coffee Shop        Sandwich Place                   Pub   
162           Coffee Shop                  Café                 Hotel   
165                 Hotel        Sandwich Place           Coffee Shop   
166              Beer Bar          Cocktail Bar    Italian Restaurant   
167                  Café           Coffee Shop               Theater   
281                  Café              Beer Bar  Gym / Fitness Center   
285                  Café         Grocery Store           Coffee Shop   
302                  Café           Coffee Shop                 Hotel   
303           Coffee Shop                  Café             Bookstore   
306                   Pub           Coffee Shop                 Hotel   
313                   Pub                 Hotel          Burger Joint   

    4th Most Common Venue  5th Most Common Venue   6th Most Common Venue  \
155          Burger Joint  Vietnamese Restaurant                     Pub   
158    Italian Restaurant         Sandwich Place                   Hotel   
161                  Café   Gym / Fitness Center           Grocery Store   
162                   Pub         Sandwich Place      Italian Restaurant   
165        Breakfast Spot         Chocolate Shop               Hotel Bar   
166    Mexican Restaurant                    Pub  Furniture / Home Store   
167           Yoga Studio     Falafel Restaurant                   Canal   
281           Coffee Shop          Grocery Store     Japanese Restaurant   
285        Sandwich Place    Lebanese Restaurant    Gym / Fitness Center   
302                   Pub           Burger Joint      Italian Restaurant   
303                   Pub                   Park                   Plaza   
306                  Café                 Garden             Pizza Place   
313        History Museum            Coffee Shop             Yoga Studio   

    7th Most Common Venue 8th Most Common Venue 9th Most Common Venue  \
155         Train Station        Chocolate Shop          Cocktail Bar   
158                 Plaza      Sushi Restaurant            Restaurant   
161   Japanese Restaurant            Hookah Bar                 Hotel   
162          Burger Joint         Train Station        Breakfast Spot   
165              Beer Bar                   Bar                  Café   
166      Tapas Restaurant      Malay Restaurant             Gastropub   
167                   Pub                 Plaza        Cricket Ground   
281  Fast Food Restaurant                 Canal     Fish & Chips Shop   
285              Beer Bar                 Plaza           Salad Place   
302           Pizza Place         Train Station                   Gym   
303                 Hotel                Garden     Fish & Chips Shop   
306          Cocktail Bar             Bookstore    Italian Resta

In [55]:
london_merged.loc[london_merged['Cluster Labels'] == 3].describe()

Latitude  Longitude  Average Income  Cluster Labels
count  13.000000  13.000000       13.000000            13.0
mean   51.527039  -0.139369    40701.757350             3.0
std     0.004202   0.022719     1279.754107             0.0
min    51.521587  -0.174992    39218.918919             3.0
25%    51.524196  -0.167818    39800.000000             3.0
50%    51.527787  -0.125739    40227.272727             3.0
75%    51.530418  -0.124590    41300.000000             3.0
max    51.535233  -0.117620    43450.847458             3.0

In [56]:
london_merged.loc[london_merged['Cluster Labels'] == 4, london_merged.columns[[5, 4] + list(range(6, london_merged.shape[1]))]]

Neighborhood  Average Income  Cluster Labels  \
2       E1 Hoxton East & Shoreditch    54300.000000               4   
4      E1 Spitalfields & Banglatown    53360.930233               4   
11      E2 Hoxton East & Shoreditch    54207.692308               4   
16                     EC1A Bunhill    53800.000000               4   
18                 EC1A Clerkenwell    53800.000000               4   
21                     EC1M Bunhill    53800.000000               4   
22                 EC1M Clerkenwell    53800.000000               4   
27                 EC1N Clerkenwell    53800.000000               4   
30                 EC1P Clerkenwell    53800.000000               4   
31                 EC1R Clerkenwell    53286.725664               4   
34                 EC1V Clerkenwell    53442.465753               4   
35    EC1V Hoxton East & Shoreditch    54300.000000               4   
36                 EC1V Hoxton West    54166.666667               4   
39                 EC1Y Clerkenwell    53800.000000               4   
44                 EC2A Clerkenwell    53800.000000               4   
45    EC2A Hoxton East & Shoreditch    54300.000000               4   
49                 EC2M Clerkenwell    53800.000000               4   
52    EC2M Hoxton East & Shoreditch    54300.000000               4   
53   EC2M Spitalfields & Banglatown    53100.000000               4   
56                 EC2N Clerkenwell    53800.000000               4   
62                 EC2P Clerkenwell    53800.000000               4   
66                 EC2R Clerkenwell    53800.000000               4   
75                 EC2V Clerkenwell    53800.000000               4   
82                 EC2Y Clerkenwell    53800.000000               4   
87                 EC3A Clerkenwell    53800.000000               4   
97                 EC3N Clerkenwell    53800.000000               4   
102                EC3P Clerkenwell    53800.000000               4   
107                EC3R Clerkenwell    53800.000000               4   
111                EC3V Clerkenwell    53800.000000               4   
117                EC4A Clerkenwell    53800.000000               4   
123                EC4M Clerkenwell    53800.000000               4   
128                EC4N Clerkenwell    53800.000000               4   
133                EC4P Clerkenwell    53800.000000               4   
136                EC4R Clerkenwell    53800.000000               4   
142                EC4V Clerkenwell    53800.000000               4   
147                EC4Y Clerkenwell    53800.000000               4   
150                    N1 Barnsbury    52743.783784               4   
153     N1 Hoxton East & Shoreditch    53965.714286               4   
154                  N1 Hoxton West    53811.328125               4   
169                    SE1 Bishop's    53569.172932               4   
171                     SE1 Chaucer    53968.750000               4   
175                    SE1 Prince's    53041.666667               4   
180                   SE11 Prince's    52737.391304               4   
188                 SW11 Queenstown    54100.000000               4   
189                 SW1A Queenstown    54100.000000               4   
191                 SW1E Queenstown    54100.000000               4   
195                 SW1H Queenstown    54100.000000               4   
197                 SW1P Queenstown    54100.000000               4   
199             SW1P Vincent Square    54633.333333               4   
201                 SW1V Queenstown    54100.000000               4   
202                  SW1V Tachbrook    53635.087719               4   
203             SW1V Vincent Square    54975.609756               4   
207                 SW1W Queenstown    54100.000000               4   
213                 SW1X Queenstown    54100.000000               4   
215                 SW1Y Queenstown    54100.000000               4   
225                SW5 Earl's Court    53884.65

In [57]:
london_merged.loc[london_merged['Cluster Labels'] == 4].describe()

Latitude  Longitude  Average Income  Cluster Labels
count  87.000000  87.000000       87.000000            87.0
mean   51.514776  -0.115795    53862.147252             4.0
std     0.016658   0.019209      314.377061             0.0
min    51.477296  -0.194095    52737.391304             4.0
25%    51.513265  -0.133679    53800.000000             4.0
50%    51.524565  -0.112042    53800.000000             4.0
75%    51.524565  -0.112026    54000.000000             4.0
max    51.534267  -0.073411    54975.609756             4.0

In [58]:
london_merged.loc[london_merged['Cluster Labels'] == 5, london_merged.columns[[5, 4] + list(range(6, london_merged.shape[1]))]]

Neighborhood  Average Income  Cluster Labels  \
99          EC3N St Katharine's & Wapping    70900.000000               5   
163            NW1 Marylebone High Street    71388.000000               5   
173                  SE1 North Bermondsey    74200.000000               5   
184  SE1P London Bridge & West Bermondsey    74200.000000               5   
211             SW1X Brompton & Hans Town    72600.000000               5   
214                   SW1X Royal Hospital    72600.000000               5   
230                      SW7 Queen's Gate    69660.927152               5   
238                           W11 Campden    70900.000000               5   
243            W1A Marylebone High Street    73500.000000               5   
245            W1B Marylebone High Street    71875.000000               5   
248            W1C Marylebone High Street    73500.000000               5   
254            W1G Marylebone High Street    73500.000000               5   
258            W1H Marylebone High Street    73457.407407               5   
272            W1U Marylebone High Street    73018.866080               5   
280                            W2 Campden    70900.000000               5   
288                            W8 Campden    70665.131579               5   
290                       W8 Queen's Gate    73900.000000               5   
291                           W9 Abingdon    69200.000000               5   

    1st Most Common Venue     2nd Most Common Venue  3rd Most Common Venue  \
99                  Hotel      Gym / Fitness Center                 Garden   
163                Garden               Coffee Shop            Art Gallery   
173                   Bar        Italian Restaurant                 Bakery   
184           Coffee Shop                       Pub             Restaurant   
211                  Café        Italian Restaurant                  Hotel   
214                 Hotel                Restaurant                   Café   
230                 Hotel  Mediterranean Restaurant     Italian Restaurant   
238                   Pub                      Park            Yoga Studio   
243                 Hotel                 Juice Bar                   Café   
245           Coffee Shop                      Café  Vietnamese Restaurant   
248                 Hotel                 Juice Bar         Clothing Store   
254                 Hotel         Indian Restaurant      French Restaurant   
258                 Hotel                    Bakery                   Café   
272                 Hotel                 Juice Bar                   Café   
280                   Pub        Chinese Restaurant                  Hotel   
288        Clothing Store                       Pub                   Café   
290             Juice Bar            Clothing Store                  Hotel   
291                  Café            Clothing Store         History Museum   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
99         History Museum                Castle        Scenic Lookout   
163                  Park          Tennis Court     Outdoor Sculpture   
173            Food Truck          Cocktail Bar                   Pub   
184                 Hotel  Fast Food Restaurant        Scenic Lookout   
211              Boutique           Coffee Shop         Jewelry Store   
214    Italian Restaurant              Boutique        Clothing Store   
230           Coffee Shop                   Pub            Restaurant   
238                 Hotel           Pizza Place     Indian Restaurant   
243          Burger Joint        Clothing Store     French Restaurant   
245                   Pub            Restaurant                 Hotel   
248     French Restaurant          Burger Joint                Bakery   
254    Italian Restaurant           Pizza Place                  Café   
258          Burger Joint             Juice Bar     French Restaurant   
272          Dessert Shop              Boutique           Pi

In [59]:
london_merged.loc[london_merged['Cluster Labels'] == 5].describe()

Latitude  Longitude  Average Income  Cluster Labels
count  18.000000  18.000000       18.000000            18.0
mean   51.508529  -0.153230    72220.296234             5.0
std     0.009225   0.039398     1574.836708             0.0
min    51.493981  -0.198310    69200.000000             5.0
25%    51.500909  -0.186733    70900.000000             5.0
50%    51.508884  -0.154000    72600.000000             5.0
75%    51.515492  -0.149286    73500.000000             5.0
max    51.523433  -0.075186    74200.000000             5.0

In [60]:
london_merged.loc[london_merged['Cluster Labels'] == 6, london_merged.columns[[5, 4] + list(range(6, london_merged.shape[1]))]]

Neighborhood  Average Income  Cluster Labels  \
9                    E1W Whitechapel    60700.000000               6   
13      E98 St Katharine's & Wapping    60700.000000               6   
120                  EC4A St James's    59000.000000               6   
149                  EC4Y St James's    60600.000000               6   
186                   SW10 Redcliffe    61971.428571               6   
187                     SW10 Stanley    60700.000000               6   
190                  SW1A St James's    58706.293706               6   
204                     SW1V Warwick    59839.768340               6   
208              SW1W Royal Hospital    61816.981132               6   
216                  SW1Y St James's    59000.000000               6   
218            SW3 Chelsea Riverside    58536.363636               6   
221               SW3 Royal Hospital    59336.619718               6   
223                     SW5 Abingdon    60929.411765               6   
224                   SW5 Courtfield    59234.146341               6   
226                    SW5 Redcliffe    58884.313725               6   
227         SW7 Brompton & Hans Town    60521.641791               6   
240                    W11 Pembridge    58500.000000               6   
247  W1C Bryanston and Dorset Square    60700.000000               6   
250                   W1D St James's    59000.000000               6   
256  W1H Bryanston and Dorset Square    60700.000000               6   
259                     W1H West End    59000.000000               6   
261                   W1J St James's    59000.000000               6   
273                   W1U St James's    59000.000000               6   
279   W2 Bryanston and Dorset Square    60700.000000               6   
284                W2 Lancaster Gate    60483.870968               6   
286                     W2 Pembridge    58500.000000               6   
317                  WC2A St James's    59000.000000               6   
320                  WC2B St James's    59000.000000               6   
321                     WC2B Warwick    61900.000000               6   
322                  WC2E St James's    59000.000000               6   
325                  WC2H St James's    59000.000000               6   
328                  WC2N St James's    58938.356164               6   
330                  WC2R St James's    59000.000000               6   

    1st Most Common Venue      2nd Most Common Venue 3rd Most Common Venue  \
9    Gym / Fitness Center                        Pub                  Café   
13            Coffee Shop         Italian Restaurant     Indian Restaurant   
120                   Pub                Coffee Shop        Sandwich Place   
149                   Pub                 Restaurant                 Hotel   
186    Italian Restaurant                     Garden      Tapas Restaurant   
187    Italian Restaurant                  Juice Bar          Gourmet Shop   
190                 Hotel                Art Gallery   Monument / Landmark   
204                 Hotel                        Pub    Italian Restaurant   
208                 Plaza                     Bakery    Italian Restaurant   
216                 Hotel                 Art Museum              Boutique   
218                Bakery               Burger Joint         Women's Store   
221                  Café                        Pub                 Plaza   
223                 Hotel                        Pub    Italian Restaurant   
224                 Hotel                        Pub           Coffee Shop   
226                 Hotel                       Café                Garden   
227               Exhibit         Italian Restaurant        Science Museum   
240                   Pub         Italian Restaurant        Clothing Store   
247                 Hotel             Sandwich Place            Restaurant   
250               Theater               Cocktail Bar        Ice Cream Shop   
256            

In [61]:
london_merged.loc[london_merged['Cluster Labels'] == 6].describe()

Latitude  Longitude  Average Income  Cluster Labels
count  33.000000  33.000000       33.000000            33.0
mean   51.504473  -0.147087    59754.521087             6.0
std     0.010442   0.033598     1063.888097             0.0
min    51.484493  -0.198577    58500.000000             6.0
25%    51.493085  -0.173418    59000.000000             6.0
50%    51.508721  -0.142642    59000.000000             6.0
75%    51.511870  -0.125014    60700.000000             6.0
max    51.517851  -0.067387    61971.428571             6.0

In [62]:
london_merged.loc[london_merged['Cluster Labels'] == 7, london_merged.columns[[5, 4] + list(range(6, london_merged.shape[1]))]]

Neighborhood  Average Income  Cluster Labels  \
159        NW1 Bloomsbury    46800.000000               7   
164     NW1 Regent's Park    48219.154229               7   
176  SE1 South Bermondsey    47500.000000               7   
181      SE11 St George's    48300.000000               7   
182          SE17 Faraday    44411.111111               7   
183   SE17 North Walworth    47386.826347               7   
267        W1T Bloomsbury    46875.000000               7   
298       WC1E Bloomsbury    46862.962963               7   
300       WC1H Bloomsbury    47105.681818               7   

         1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
159                Coffee Shop                   Pub                  Café   
164          Indian Restaurant           Coffee Shop                   Pub   
176  Middle Eastern Restaurant                   Pub        Breakfast Spot   
181                        Pub                  Park              Pharmacy   
182          Convenience Store           Pizza Place                   Pub   
183              Grocery Store                  Café                   Pub   
267                Coffee Shop    Italian Restaurant                 Hotel   
298                Coffee Shop               Exhibit                   Bar   
300                Coffee Shop                  Café                   Pub   

    4th Most Common Venue 5th Most Common Venue 6th Most Common Venue  \
159     Indian Restaurant                 Plaza                 Hotel   
164  Gym / Fitness Center                   Bar                Bakery   
176            Public Art    Spanish Restaurant                  Café   
181                 Plaza           Coffee Shop    Chinese Restaurant   
182            Public Art            Boxing Gym                   Gym   
183     Convenience Store   Lebanese Restaurant       Thai Restaurant   
267          Cocktail Bar           Pizza Place              Wine Bar   
298                 Plaza    Italian Restaurant       Organic Grocery   
300                 Hotel    Italian Restaurant                   Bar   

      7th Most Common Venue 8th Most Common Venue     9th Most Common Venue  \
159  Furniture / Home Store  Gym / Fitness Center              Burger Joint   
164      Italian Restaurant          Gourmet Shop                      Café   
176              Boxing Gym             Bike Shop        Chinese Restaurant   
181          Sandwich Place                  Café                       Gym   
182             Event Space            Donut Shop               Dry Cleaner   
183    Fast Food Restaurant                Market  Bike Rental / Bike Share   
267                    Café      Sushi Restaurant         French Restaurant   
298       French Restaurant          Cocktail Bar               Pizza Place   
300          Sandwich Place                 Plaza                      Park   

          10th Most Common Venue  
159              Bed & Breakfast  
164                Grocery Store  
176                  Coffee Shop  
181         Gym / Fitness Center  
182  Eastern European Restaurant  
183          Fried Chicken Joint  
267         Gym / Fitness Center  
298                        Hotel  
300         Gym / Fitness Center

In [63]:
london_merged.loc[london_merged['Cluster Labels'] == 7].describe()

Latitude  Longitude  Average Income  Cluster Labels
count   9.000000   9.000000        9.000000             9.0
mean   51.509724  -0.115282    47051.192941             7.0
std     0.017307   0.024729     1136.898395             0.0
min    51.488859  -0.141681    44411.111111             7.0
25%    51.492128  -0.135925    46862.962963             7.0
50%    51.521022  -0.129233    47105.681818             7.0
75%    51.524872  -0.090840    47500.000000             7.0
max    51.527902  -0.082095    48300.000000             7.0

In order to better evaluate the average income for each cluster, the method describe() shows the details for each cluster.

# 5. Discussion #

Considering the resulting clustering of London Zone 1 neighbourhoods, it is possible to have an insight of how the venues are distributed regarding the average income of each neighbourhood. This reports tries to identify the appropriate location to support the decision of the customer who wants to find a region with high income and with many hotels and touristic spots to open his new Bakery.

### 5.1 The Appropriate Cluster ###

Based on the k-means clustering analysis, it is possible to identify the characteristics wanted by the customer to open his new Bakery. The cluster 5 above shows a group of neighbourhoods with high average income and with Hotels between their most common venues. Athough common sense could indicate that these neighbourhoods would be right in City of London, it is possible to notice that they are distributed around Hyde Park and Kensington regions.

# 6. Conclusion #

In this study, the London Zone 1 was analysed to find the appropriate neighbourhoods for the customer who wants to open his new Bakery in a high income touristic region. The analysis distributed London neighbourhoods into clusters considering the most common venues and the average income in each neighbourhood.

This analysis could support the decision of the customer in a number of ways. Based on available data, the result can contradict the common sense that would justify the decision otherwise.